In [13]:
import pandas as pd
import folium
from folium import plugins
from folium.plugins import HeatMap
import h3
import import_ipynb
import H3_Visualization
from datetime import datetime


In this notebook we will
- explore geographical demand patterns
- visualise points of interest
- determine correlation between different points of interest and demand
- explore spatio-temporal demand patterns

# Geographical demand patterns

In [14]:
trips_df = pd.read_pickle("../00_data/trips.pkl")
stations_df = pd.read_pickle("../00_data/stations.pkl")
hexagons_df = pd.read_pickle("../00_data/hexagons.pkl")
poi_df = pd.read_pickle("../00_data/poi.pkl")


First of all we will create a heatmap representing all started trips and mark on the same map the stations. This should provide us with a rough overview of which areas in LA are most or least popular (to start the trip).

In [15]:
trips_df.columns


Index(['start_time', 'end_time', 'start_station_id', 'end_station_id',
       'bike_id', 'user_type', 'start_station_name', 'end_station_name',
       'duration', 'start_latitude', 'start_longitude', 'end_latitude',
       'end_longitude', 'distance', 'speed', 'start_hex', 'end_hex',
       'sustenance_poi_start', 'public_transport_poi_start',
       'education_poi_start', 'arts_and_culture_poi_start', 'sports_poi_start',
       'sustenance_poi_end', 'public_transport_poi_end', 'education_poi_end',
       'arts_and_culture_poi_end', 'sports_poi_end'],
      dtype='object')

In [16]:
stations_df.columns


Index(['latitude', 'longitude', 'zip_code', 'total_docks', 'is_event_based',
       'is_virtual', 'is_visible', 'station_id', 'open_time', 'close_time',
       'has_geofence', 'open_time_hour', 'open_time_minute', 'close_time_hour',
       'close_time_minute'],
      dtype='object')

In [17]:
# add joint coordinates column to plot heatmaps
trips_df["start_coordinates"] = list(
    zip(trips_df["start_latitude"].round(4), trips_df["start_longitude"].round(4))
)
trips_df["end_coordinates"] = list(
    zip(trips_df["end_latitude"].round(4), trips_df["end_longitude"].round(4))
)

stations_df["coordinates"] = list(
    zip(stations_df["latitude"].round(4), stations_df["longitude"].round(4))
)


In [18]:
# plot heatmatp for starting trips
trips_heatmap = folium.Map(
    location=(34.052235, -118.447),
    tiles="Stamen Toner",
    zoom_start=11,
    control_scale=True,
    max_zoom=20,
)

trips_heatmap.add_child(plugins.HeatMap(trips_df["start_coordinates"], radius=30))

for position in stations_df["coordinates"]:
    folium.CircleMarker(
        radius=5,
        location=position,
        popup="The Waterfront",
        color="crimson",
        fill_color="crimson",
    ).add_to(trips_heatmap)
trips_heatmap


The heatmap shows areas of higher and lower popularity.

In [19]:
hexagons_df["geometry"] = hexagons_df.apply(H3_Visualization.add_geometry, axis=1)
hexagons_df.head(2)


hex                                  hex_and_neighbors  \
0  8929a1d7577ffff  [8929a1d7563ffff, 8929a1d753bffff, 8929a1d7573...   
1  8929a1d7543ffff  [8929a1d7547ffff, 8929a1d7557ffff, 8929a1d755b...   

   sustenance_poi  public_transport_poi  education_poi  arts_and_culture_poi  \
0              80                    28              2                     4   
1              40                     1              2                     0   

   sports_poi                                           geometry  
0           0  POLYGON ((-118.24326787807875 34.0489105491889...  
1           1  POLYGON ((-118.23278211407867 34.0442939104639...

In [20]:
def calculate_hexagon_trips(label, group_by):
    hexagons_df[label] = trips_df.groupby(group_by).size()
    hexagons_df[label] = hexagons_df[label].fillna(value=0)


In [21]:
hexagons_df = hexagons_df.set_index("hex")

calculate_hexagon_trips(label="incoming_trips", group_by="start_hex")
calculate_hexagon_trips(label="outgoing_trips", group_by="end_hex")

hexagons_df = hexagons_df.reset_index()
hexagons_df.head(2)


hex                                  hex_and_neighbors  \
0  8929a1d7577ffff  [8929a1d7563ffff, 8929a1d753bffff, 8929a1d7573...   
1  8929a1d7543ffff  [8929a1d7547ffff, 8929a1d7557ffff, 8929a1d755b...   

   sustenance_poi  public_transport_poi  education_poi  arts_and_culture_poi  \
0              80                    28              2                     4   
1              40                     1              2                     0   

   sports_poi                                           geometry  \
0           0  POLYGON ((-118.24326787807875 34.0489105491889...   
1           1  POLYGON ((-118.23278211407867 34.0442939104639...   

   incoming_trips  outgoing_trips  
0           12796           11117  
1            3468            3527

In [22]:
def convert_to_hex(latitude, longitude):
    return h3.geo_to_h3(lat=latitude, lng=longitude, resolution=9)


In [23]:
stations_df["hex"] = stations_df.apply(
    lambda station: convert_to_hex(station["latitude"], station["longitude"]), axis=1
)
stations_df = pd.merge(stations_df, hexagons_df, left_on="hex", right_on="hex")
stations_df.head(2)


latitude  longitude zip_code  total_docks  is_event_based  is_virtual  \
0  34.04850 -118.25854    90017           31           False       False   
1  34.04554 -118.25667    90014           31           False       False   

   is_visible  station_id open_time close_time  ...              hex  \
0       False        3005  05:45:00   05:39:00  ...  8929a1d62cbffff   
1       False        3006  05:45:00   05:39:00  ...  8929a1d75afffff   

                                   hex_and_neighbors  sustenance_poi  \
0  [8929a1d62c3ffff, 8929a1d62cfffff, 8929a1d62db...              80   
1  [8929a1d75a7ffff, 8929a1d62dbffff, 8929a1d75a3...             102   

   public_transport_poi  education_poi arts_and_culture_poi sports_poi  \
0                    34              1                    1          5   
1                    59              0                    5          6   

                                            geometry  incoming_trips  \
0  POLYGON ((-118.2571266163185 34.04843946446993...           13337   
1  POLYGON ((-118.25357007023374 34.0435886657656...            6304   

   outgoing_trips  
0           14189  
1            6569  

[2 rows x 26 columns]

In [42]:
variable = "outgoing_trips"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "demand"},
    range_color=(0, hexagons_df[variable].quantile(0.9)),
    palette="greens",
)
fig.show()


# Visualising points of interest

In [25]:
variable = "sustenance_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "sustenance"},
    range_color=(0, hexagons_df[variable].max()),
    palette="greens",
)
fig.show()


In [26]:
variable = "public_transport_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "public transport"},
    range_color=(0, hexagons_df[variable].max()),
    palette="reds",
)
fig.show()


In [27]:
variable = "education_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "education"},
    range_color=(0, hexagons_df[variable].max()),
    palette="blues",
)
fig.show()

In [28]:
variable = "arts_and_culture_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "arts & culture"},
    range_color=(0, hexagons_df[variable].max()),
    palette="oranges",
)
fig.show()

In [29]:
variable = "sports_poi"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "sports"},
    range_color=(0, hexagons_df[variable].max()),
    palette="purples",
)
fig.show()

# Correlation between different points of interest and demand

In [30]:
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler


In [31]:
input_features = stations_df[
    [
        "sustenance_poi",
        "public_transport_poi",
        "education_poi",
        "arts_and_culture_poi",
        "sports_poi",
    ]
]
predicted_variable = stations_df["outgoing_trips"]


In [32]:
scaler = StandardScaler()
input_features_scaled = scaler.fit_transform(input_features)


In [33]:
reg = LinearRegression().fit(input_features_scaled, predicted_variable)
reg.score(input_features_scaled, predicted_variable)


0.5913646295598255

In [34]:
reg.coef_


array([1114.41991424,  886.31181877,  -59.91933457,  523.40506598,
        284.24181689])

In [ ]:
predicted_variable = stations_df["outgoing_trips"]

# Spatio-temporal demand patterns
Additionally, we are interested which areas are most popular to start and end trips. This information is very usefull to fleat operations, which plan and coordinate bikes relocations, to meet the highest demand.

In [35]:
hexagons_df["trips_difference"] = (
    hexagons_df["incoming_trips"] - hexagons_df["outgoing_trips"]
)


In [36]:
variable = "trips_difference"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips difference"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()


In [37]:
def calculate_hexagon_trips_by_hours(label, group_by, hours):
    hexagons_df[label] = (
        trips_df[
            (trips_df["start_time"].dt.hour >= hours[0])
            & (trips_df["start_time"].dt.hour <= hours[1])
        ]
        .groupby(group_by)
        .size()
    )
    hexagons_df[label] = hexagons_df[label].fillna(value=0)


In [38]:
hexagons_df = hexagons_df.set_index("hex")
now = datetime.now()
morning_hours = [now.replace(hour=6).hour, now.replace(hour=12).hour]
evening_hours = [now.replace(hour=14).hour, now.replace(hour=20).hour]

calculate_hexagon_trips_by_hours(
    label="incoming_trips_morning", group_by="start_hex", hours=morning_hours
)
calculate_hexagon_trips_by_hours(
    label="outgoing_trips_morning", group_by="end_hex", hours=morning_hours
)
calculate_hexagon_trips_by_hours(
    label="incoming_trips_evening", group_by="start_hex", hours=evening_hours
)
calculate_hexagon_trips_by_hours(
    label="outgoing_trips_evening", group_by="end_hex", hours=evening_hours
)

hexagons_df["trips_difference_morning"] = (
    hexagons_df["incoming_trips_morning"] - hexagons_df["outgoing_trips_morning"]
)
hexagons_df["trips_difference_evening"] = (
    hexagons_df["incoming_trips_evening"] - hexagons_df["outgoing_trips_evening"]
)

hexagons_df = hexagons_df.reset_index()
hexagons_df.head(2)


hex                                  hex_and_neighbors  \
0  8929a1d7577ffff  [8929a1d7563ffff, 8929a1d753bffff, 8929a1d7573...   
1  8929a1d7543ffff  [8929a1d7547ffff, 8929a1d7557ffff, 8929a1d755b...   

   sustenance_poi  public_transport_poi  education_poi  arts_and_culture_poi  \
0              80                    28              2                     4   
1              40                     1              2                     0   

   sports_poi                                           geometry  \
0           0  POLYGON ((-118.24326787807875 34.0489105491889...   
1           1  POLYGON ((-118.23278211407867 34.0442939104639...   

   incoming_trips  outgoing_trips  trips_difference  incoming_trips_morning  \
0           12796           11117              1679                  3079.0   
1            3468            3527               -59                  1302.0   

   outgoing_trips_morning  incoming_trips_evening  outgoing_trips_evening  \
0                  8334.0                    8537                    1759   
1                  1227.0                    1585                    1605   

   trips_difference_morning  trips_difference_evening  
0                   -5255.0                      6778  
1                      75.0                       -20

In [39]:
variable = "trips_difference_morning"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips diff. morning"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()


In [40]:
variable = "trips_difference_evening"
fig = H3_Visualization.plot_frequency(
    dataset=hexagons_df,
    variable=variable,
    labels={variable: "trips diff. evening"},
    range_color=(
        -hexagons_df[variable].quantile(0.9),
        hexagons_df[variable].quantile(0.9),
    ),
)
fig.show()
